In [0]:
import json
import re
import pyspark.pandas as pd
import numpy as np
# import snowflake.connector
from cryptography.hazmat.backends import default_backend
from cryptography.hazmat.primitives import serialization
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark.sql.window import Window

In [0]:
%sql
  select * from hive_metastore.analytics.orig_fee_amort_raw_check

LOAN_ID ORIGINATING_BANK IR TRANSACTION_AMOUNT TERM ORIGINATION_DATE ORIGINAL_MATURITY_DATE LOAN_AMOUNT PRINCIPAL_BALANCE TRANSACTION_DATE REVERSAL_DATE REVERSAL_AMOUNT EARLY_PAID_AT SOLD_DATE TRANSREFNO MAX_REPORT_DATE MAX_DWH_TIMESTAMP AMORT_TYPE MONTH_NUM IPMT PERIOD_START_DATE DAYS_OF_PERIOD DAY_NUM IPMT_D REPORT_DATE AMORT_SHARE CUM_SHARE CUM_SHARE_LAG ORIG_FEE_AMORT CUM_ORIG_FEE_AMORT DEFERRED_ORIG_FEE LOAN_SALE_ENDING_BAL REVERSAL_AFTER_SOLD_LOAN DWH_FLAG 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 1 0.5267684541899582 2020-02-09 0.005571180131195652 0.005571180131195652 null 0.08713325725189999 0.08713325725189999 15.552866742748101 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 2 0.5267684541899582 2020-02-10 0.005571180131195652 0.011142360262391304 0.005571180131195652 0.08713325725189999 0.17426651450379999 15.4657334854962 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 3 0.5267684541899582 2020-02-11 0.005571180131195652 0.016713540393586954 0.011142360262391304 0.08713325725189999 0.26139977175569995 15.3786002282443 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 4 0.5267684541899582 2020-02-12 0.005571180131195652 0.022284720524782607 0.016713540393586954 0.08713325725189999 0.34853302900759997 15.291466970992401 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 5 0.5267684541899582 2020-02-13 0.005571180131195652 0.02785590065597826 0.022284720524782607 0.08713325725189999 0.4356662862595 15.2043337137405 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 6 0.5267684541899582 2020-02-14 0.005571180131195652 0.033427080787173914 0.02785590065597826 0.08713325725189999 0.5227995435114 15.1172004564886 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 7 0.5267684541899582 2020-02-15 0.005571180131195652 0.03899826091836957 0.033427080787173914 0.08713325725189999 0.6099328007633 15.0300671992367 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 8 0.5267684541899582 2020-02-16 0.005571180131195652 0.04456944104956522 0.03899826091836957 0.08713325725189999 0.6970660580152 14.942933941984801 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 9 0.5267684541899582 2020-02-17 0.005571180131195652 0.050140621180760875 0.04456944104956522 0.08713325725189999 0.7841993152671001 14.8558006847329 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 10 0.5267684541899582 2020-02-18 0.005571180131195652 0.05571180131195653 0.050140621180760875 0.08713325725189999 0.8713325725190001 14.768667427481 0 0 N 50678529 CBW 0.22972433 15.64 11 2020-02-09 2021-01-09 797.98 0.0 2020-02-09 null null null null 7539519 2023-05-16 2023-05-17T17:23:03.250+0000 baseline 1 15.276285 2020-02-09 29 11 0.526

In [0]:
df_base = _sqldf

In [0]:
%sql
 select * from hive_metastore.analytics.ds_orig_fee_data_input_t
  where dwh_flag = 'U'

loan_id originating_bank ir transaction_amount term origination_date original_maturity_date loan_amount principal_balance transaction_date reversal_date reversal_amount early_paid_at sold_date transrefno max_report_date max_dwh_timestamp dwh_flag 65278629 CBW 0.08867025 89.8 24 2022-01-02 2024-01-02 4579.85 0.00 2022-01-02T16:27:49.000+0000 null null 2023-06-08T00:00:00.000+0000 null 23203507 2023-06-07 2023-06-08T12:30:42.882+0000 U 63863062 CBW 0.08869554 58.98 24 2021-09-25 2023-09-25 3008.22 0.00 2021-09-25T17:23:42.000+0000 null null 2023-06-08T00:00:00.000+0000 2021-09-29 18485321 2023-06-07 2023-06-08T12:30:42.882+0000 U 70355060 CBW 0.27082293 30.29 18 2022-01-21 2023-07-21 1544.90 0.00 2022-01-21T16:39:05.000+0000 null null 2023-06-08T00:00:00.000+0000 null 24227560 2023-06-07 2023-06-08T12:30:42.882+0000 U 62938930 CBW 0.26003541 44.08 24 2021-07-21 2023-07-21 2248.11 0.00 2021-07-22T00:31:49.000+0000 null null 2023-06-08T00:00:00.000+0000 2021-07-30 15955950 2023-06-07 2023-06-08T12:30:42.882+0000 U 63621968 CBW 0.23999269 41.72 24 2021-09-07 2023-09-07 2128.20 0.00 2021-09-07T17:26:18.000+0000 null null 2023-06-08T00:00:00.000+0000 2021-09-15 17726000 2023-06-07 2023-06-08T12:30:42.882+0000 U 62358145 CBW 0.24578397 62.1 24 2021-06-11 2023-06-11 3167.40 0.00 2021-06-11T17:27:39.000+0000 null null 2023-06-08T00:00:00.000+0000 null 14759694 2023-06-07 2023-06-08T12:30:42.882+0000 U 65276533 CBW 0.29486949 22.67 24 2022-01-02 2024-01-02 1156.35 0.00 2022-01-02T16:19:15.000+0000 null null 2023-06-08T00:00:00.000+0000 null 23201907 2023-06-07 2023-06-08T12:30:42.882+0000 U 62722113 CBW 0.24577535 68.34 24 2021-07-06 2023-07-06 3485.71 0.00 2021-07-06T17:34:22.000+0000 null null 2023-06-08T00:00:00.000+0000 null 15462513 2023-06-07 2023-06-08T12:30:42.882+0000 U

In [0]:
# load new repords into dataframe
df = _sqldf

In [0]:
new_column_name_list= list(map(lambda x: x.upper(), df.columns))
df = df.toDF(*new_column_name_list)
print(new_column_name_list)

['LOAN_ID', 'ORIGINATING_BANK', 'IR', 'TRANSACTION_AMOUNT', 'TERM', 'ORIGINATION_DATE', 'ORIGINAL_MATURITY_DATE', 'LOAN_AMOUNT', 'PRINCIPAL_BALANCE', 'TRANSACTION_DATE', 'REVERSAL_DATE', 'REVERSAL_AMOUNT', 'EARLY_PAID_AT', 'SOLD_DATE', 'TRANSREFNO', 'MAX_REPORT_DATE', 'MAX_DWH_TIMESTAMP', 'DWH_FLAG']


In [0]:
# change columns with decimal type to float

df = df.withColumn('IR',df['IR'].cast('double'))\
       .withColumn('TERM',df['TERM'].cast('int'))\
       .withColumn('LOAN_AMOUNT',df['LOAN_AMOUNT'].cast('double'))\
       .withColumn('TRANSACTION_AMOUNT',df['TRANSACTION_AMOUNT'].cast('double'))\
       .withColumn('REVERSAL_AMOUNT',df['REVERSAL_AMOUNT'].cast('double'))\
       .withColumn('PRINCIPAL_BALANCE',df['PRINCIPAL_BALANCE'].cast('double'))\
       .withColumn('EARLY_PAID_AT', df['EARLY_PAID_AT'].cast('date'))\
       .withColumn('TRANSACTION_DATE',df['TRANSACTION_DATE'].cast('date'))\
       .withColumn('REVERSAL_DATE',df['REVERSAL_DATE'].cast('date'))


In [0]:
# assign amortization type to each loan
#canceled loan will be refunded at the canceled date(pbo=0)

df = df.withColumn('AMORT_TYPE',when(col('IR').isNull(),'non-amortizable')\
                                .when(~col('REVERSAL_DATE').isNull(),'reversal')\
                                .when(col('EARLY_PAID_AT').isNull(),'baseline')\
                                .when((~col('EARLY_PAID_AT').isNull()) & (col('PRINCIPAL_BALANCE')>0),'baseline')\
                                .otherwise('accelerated'))

In [0]:
# create python function that returns monthly interest paid
# rate = IR 
# per = nth payment period (1 to 24)
# nper = adj_term
# pv= loan_amount
def ipmt(rate, per, nper, pv):
    if rate != 0:
        pmt = (rate*(pv*(1+ rate)**nper))/(1*(1-(1+ rate)**nper))
    else:
        pmt = (-1*(pv)/nper)
        
    ipmt = (((1+rate)**(per-1)) * (pv*rate + pmt) - pmt)
    
    return ipmt

# create pyspark udf that returns monthly interest paid
udf_ipmt= udf(ipmt, FloatType())

In [0]:
# create df that contains consecutive integers
day_nbs = spark.range(
    1, 32, 1
).toDF("DAY_NUM")
day_nbs = day_nbs.withColumn('DAY_NUM',day_nbs['DAY_NUM'].cast('int'))

month_nbs = spark.range(
    1, 25, 1
).toDF("MONTH_NUM")
month_nbs = month_nbs.withColumn('MONTH_NUM',month_nbs['MONTH_NUM'].cast('int'))

In [0]:
### Initialize amortization schedule for new loans
df_new = df.drop(col('DWH_FLAG'))
#.filter(col('TRANSACTION_DATE')>='2023-01-01')
print(df_new.count())

8


In [0]:
# create new row for each period for each loan
# (This will handle new amortization schedule for all new loans and new transactions for existing loans)
df_new = df_new.join(month_nbs,(month_nbs.MONTH_NUM >= 1) & (month_nbs.MONTH_NUM <= df_new.TERM), 'left')

In [0]:
# monthly amortization 
df_amort = df_new.filter(col('IR') > 0)\
                 .withColumn('IPMT',
                             udf_ipmt((col('IR')/12), col('MONTH_NUM'), col('TERM'), col('LOAN_AMOUNT')))\
                 .withColumn('PERIOD_START_DATE',
                             add_months(col('ORIGINATION_DATE'), col('MONTH_NUM') - 1))\
                 .withColumn('DAYS_OF_PERIOD',
                             datediff(add_months(col('ORIGINATION_DATE'), col('MONTH_NUM')), add_months(col('ORIGINATION_DATE'), col('MONTH_NUM') - 1)))

In [0]:
# create new row for each day of each period for each loan
df_amort = df_amort.join(day_nbs,(day_nbs.DAY_NUM >= 1) & (day_nbs.DAY_NUM <= df_amort.DAYS_OF_PERIOD), 'left')

df_amort = df_amort.withColumn('IPMT_D',col('IPMT')/col('DAYS_OF_PERIOD'))\
                   .withColumn('REPORT_DATE',date_add(col('PERIOD_START_DATE'), col('DAY_NUM') - 1))

In [0]:
# calculate the daily amortization share and daily origination cost amortized
df_amort = df_amort.withColumn('AMORT_SHARE',
                                     col('IPMT_D')/sum(col('IPMT_D')).over(Window.partitionBy(col('LOAN_ID'),col('TRANSACTION_DATE'),col('AMORT_TYPE'))))\
                   .withColumn('CUM_SHARE',
                                     sum(col('AMORT_SHARE')).over(Window.partitionBy(col('LOAN_ID'),col('TRANSACTION_DATE'),col('AMORT_TYPE')).orderBy(col('REPORT_DATE').asc()).rowsBetween(Window.unboundedPreceding, Window.currentRow)))\
                   .withColumn('CUM_SHARE_LAG',
                                     lag(col('CUM_SHARE'),1).over(Window.partitionBy(col('LOAN_ID'),col('TRANSACTION_DATE'),col('AMORT_TYPE')).orderBy(col('REPORT_DATE').asc())))\
                   .withColumn('AMORT_SHARE',
                                     when(col('REPORT_DATE') < col('TRANSACTION_DATE'),lit('0'))\
                                    .when(col('REPORT_DATE') == col('TRANSACTION_DATE'),col('CUM_SHARE'))\
                                    .otherwise(col('AMORT_SHARE')))

In [0]:
prefix = "U_"
for column in df.columns:
    df = df.withColumnRenamed(column, prefix + column)

In [0]:
df_old = df_base.join(df,(df_base.LOAN_ID == df.U_LOAN_ID) & (df_base.TRANSREFNO == df.U_TRANSREFNO),'left')
df_old_keep = df_old.filter(col('U_LOAN_ID').isNull()).drop(* df.columns)
#print(df_old.count(),df_old_keep.count())
#df_old_keep.printSchema()

In [0]:
sold_amort = df_amort.filter((~col('SOLD_DATE').isNull()) & ((col('REPORT_DATE') <= col('SOLD_DATE'))|(col('REPORT_DATE')==col('REVERSAL_DATE'))))

In [0]:
# calculate amort share at sold date
sold_amort = sold_amort.withColumn('AMORT_SHARE',
                                    when(col('REPORT_DATE') == col('SOLD_DATE'), 1 - col('CUM_SHARE_LAG'))\
                                    .when(col('REPORT_DATE') == col('REVERSAL_DATE'),lit('0'))\
                                    .otherwise(col('AMORT_SHARE')))

In [0]:
# calculate daily origination cost amortized, cumulative amortized cost, unearned balance, loan sale ending balance
sold_amort = sold_amort.withColumn('ORIG_FEE_AMORT', 
                                    when(col('REPORT_DATE') == col('SOLD_DATE'), 0)\
                                    .when(col('REPORT_DATE') == col('REVERSAL_DATE'),lit('0'))\
                                     .otherwise(col('TRANSACTION_AMOUNT') * col('AMORT_SHARE')))\
                        .withColumn('CUM_ORIG_FEE_AMORT',
                                    sum(col('ORIG_FEE_AMORT')).over(Window.partitionBy(col('LOAN_ID'),col('AMORT_TYPE')).orderBy(col('REPORT_DATE').asc()).rowsBetween(Window.unboundedPreceding, Window.currentRow)))\
                        .withColumn('DEFERRED_ORIG_FEE', 
                                    when((col('REPORT_DATE') == col('SOLD_DATE')) |(col('CUM_SHARE') == 0), 0)\
                                    .when(col('REPORT_DATE') == col('REVERSAL_DATE'),lit('0'))\
                                     .otherwise(col('TRANSACTION_AMOUNT') * (1 - col('CUM_SHARE'))))\
                        .withColumn('LOAN_SALE_ENDING_BAL',
                                    when(col('REPORT_DATE') == col('SOLD_DATE'), col('TRANSACTION_AMOUNT') * col('AMORT_SHARE'))\
                                    .when(col('REPORT_DATE') == col('REVERSAL_DATE'),lit('0'))\
                                     .otherwise(0))\
                        .withColumn('REVERSAL_AFTER_SOLD_LOAN',
                                    when(col('REPORT_DATE')==col('REVERSAL_DATE'),-1 * col('TRANSACTION_AMOUNT'))\
                                    .otherwise(lit('0')))\
                        .withColumn('DWH_FLAG',lit('U'))

In [0]:
base_amort = df_amort.filter((col('AMORT_TYPE') == 'baseline') & (col('SOLD_DATE').isNull()))

In [0]:
# calculate amort share at last day
base_amort = base_amort.withColumn('AMORT_SHARE',
                                    when((col('MONTH_NUM') == col('TERM')) & (col('DAY_NUM') == col('DAYS_OF_PERIOD')), 1-col('CUM_SHARE_LAG'))\
                                     .otherwise(col('AMORT_SHARE')))

In [0]:
# calculate daily origination cost amortized, cumulative amortized cost, unearned balance, loan sale ending balance
base_amort = base_amort.withColumn('ORIG_FEE_AMORT', col('TRANSACTION_AMOUNT') * col('AMORT_SHARE'))\
                       .withColumn('CUM_ORIG_FEE_AMORT',
                                    when((col('MONTH_NUM') == col('TERM')) & (col('DAY_NUM') == col('DAYS_OF_PERIOD')), col('TRANSACTION_AMOUNT'))\
                                    .otherwise(sum(col('ORIG_FEE_AMORT')).over(Window.partitionBy(col('LOAN_ID'),col('AMORT_TYPE')).orderBy(col('REPORT_DATE').asc()).rowsBetween(Window.unboundedPreceding, Window.currentRow))))\
                        .withColumn('DEFERRED_ORIG_FEE', 
                                    when((col('CUM_SHARE') == 0) |(col('REPORT_DATE') < col('TRANSACTION_DATE')),lit('0'))
                                    .otherwise(col('TRANSACTION_AMOUNT') - col('CUM_ORIG_FEE_AMORT')))\
                        .withColumn('LOAN_SALE_ENDING_BAL',lit(0))\
                        .withColumn('REVERSAL_AFTER_SOLD_LOAN',lit('0'))\
                        .withColumn('DWH_FLAG',lit('U'))

In [0]:
accel_amort = df_amort.filter((col('AMORT_TYPE') == 'accelerated') & (col('SOLD_DATE').isNull()) & (col('REPORT_DATE') <= col('EARLY_PAID_AT')))

In [0]:
accel_amort = accel_amort.withColumn('AMORT_SHARE',
                                    when(col('REPORT_DATE') == col('EARLY_PAID_AT'), 1-col('CUM_SHARE_LAG')).\
                                      otherwise(col('AMORT_SHARE')))

In [0]:
# calculate daily origination cost amortized, cumulative amortized cost, unearned balance, loan sale ending balance
accel_amort = accel_amort.withColumn('ORIG_FEE_AMORT', col('TRANSACTION_AMOUNT') * col('AMORT_SHARE'))\
                        .withColumn('CUM_ORIG_FEE_AMORT',
                                   when(col('REPORT_DATE') == col('EARLY_PAID_AT'), col('TRANSACTION_AMOUNT'))\
                                    .otherwise(sum(col('ORIG_FEE_AMORT')).over(Window.partitionBy(col('LOAN_ID')).orderBy(col('REPORT_DATE').asc()).rowsBetween(Window.unboundedPreceding, Window.currentRow))))\
                        .withColumn('DEFERRED_ORIG_FEE', 
                                    when((col('CUM_SHARE') == 0) |(col('REPORT_DATE') < col('TRANSACTION_DATE')),lit('0'))
                                    .otherwise(col('TRANSACTION_AMOUNT') - col('CUM_ORIG_FEE_AMORT')))\
                        .withColumn('LOAN_SALE_ENDING_BAL', lit(0))\
                        .withColumn('REVERSAL_AFTER_SOLD_LOAN',lit('0'))\
                        .withColumn('DWH_FLAG',lit('U'))

In [0]:
reverse_amort = df_amort.filter((col('AMORT_TYPE') == 'reversal') & (col('SOLD_DATE').isNull()) & (col('REPORT_DATE') <= col('REVERSAL_DATE')))

In [0]:
reverse_amort = reverse_amort.withColumn('AMORT_SHARE',
                                    when(col('REPORT_DATE') > least(col('EARLY_PAID_AT'),col('REVERSAL_DATE')), lit('0'))\
                                    .when((col('REPORT_DATE') == col('EARLY_PAID_AT')) & (col('REVERSAL_DATE')>col('EARLY_PAID_AT')),1-col('CUM_SHARE_LAG'))\
                                    .otherwise(col('AMORT_SHARE')))\
                   .withColumn('CUM_SHARE',
                                     sum(col('AMORT_SHARE')).over(Window.partitionBy(col('LOAN_ID'),col('TRANSACTION_DATE')).orderBy(col('REPORT_DATE').asc()).rowsBetween(Window.unboundedPreceding, Window.currentRow)))\
                   .withColumn('CUM_SHARE_LAG',
                                     lag(col('CUM_SHARE'),1).over(Window.partitionBy(col('LOAN_ID'),col('TRANSACTION_DATE')).orderBy(col('REPORT_DATE').asc())))\
                   .withColumn('AMORT_SHARE',
                                  when(col('REPORT_DATE') == col('REVERSAL_DATE'), -col('CUM_SHARE_LAG'))
                                  .otherwise(col('AMORT_SHARE')))

In [0]:
# calculate daily origination cost amortized, cumulative amortized cost, unearned balance, loan sale ending balance
reverse_amort = reverse_amort.withColumn('ORIG_FEE_AMORT', col('TRANSACTION_AMOUNT') * col('AMORT_SHARE'))\
                        .withColumn('CUM_ORIG_FEE_AMORT',
                                   when(col('REPORT_DATE') == col('REVERSAL_DATE'), col('TRANSACTION_AMOUNT'))\
                                    .otherwise(sum(col('ORIG_FEE_AMORT')).over(Window.partitionBy(col('LOAN_ID'),col('TRANSACTION_DATE')).orderBy(col('REPORT_DATE').asc()).rowsBetween(Window.unboundedPreceding, Window.currentRow))))\
                        .withColumn('DEFERRED_ORIG_FEE', 
                                    when((col('CUM_SHARE') == 0) |(col('REPORT_DATE') < col('TRANSACTION_DATE')),lit('0'))
                                    .otherwise(col('TRANSACTION_AMOUNT') - col('CUM_ORIG_FEE_AMORT')))\
                        .withColumn('LOAN_SALE_ENDING_BAL', lit(0))\
                        .withColumn('REVERSAL_AFTER_SOLD_LOAN',lit('0'))\
                        .withColumn('DWH_FLAG',lit('U'))

In [0]:
base_amort.printSchema()

root
 |-- LOAN_ID: string (nullable = true)
 |-- ORIGINATING_BANK: string (nullable = true)
 |-- IR: double (nullable = true)
 |-- TRANSACTION_AMOUNT: double (nullable = true)
 |-- TERM: integer (nullable = true)
 |-- ORIGINATION_DATE: date (nullable = true)
 |-- ORIGINAL_MATURITY_DATE: date (nullable = true)
 |-- LOAN_AMOUNT: double (nullable = true)
 |-- PRINCIPAL_BALANCE: double (nullable = true)
 |-- TRANSACTION_DATE: date (nullable = true)
 |-- REVERSAL_DATE: date (nullable = true)
 |-- REVERSAL_AMOUNT: double (nullable = true)
 |-- EARLY_PAID_AT: date (nullable = true)
 |-- SOLD_DATE: date (nullable = true)
 |-- TRANSREFNO: string (nullable = true)
 |-- MAX_REPORT_DATE: date (nullable = true)
 |-- MAX_DWH_TIMESTAMP: timestamp (nullable = true)
 |-- AMORT_TYPE: string (nullable = false)
 |-- MONTH_NUM: integer (nullable = true)
 |-- IPMT: float (nullable = true)
 |-- PERIOD_START_DATE: date (nullable = true)
 |-- DAYS_OF_PERIOD: integer (nullable = true)
 |-- DAY_NUM: integer (nul

In [0]:
df_old_keep.printSchema()

root
 |-- LOAN_ID: string (nullable = true)
 |-- ORIGINATING_BANK: string (nullable = true)
 |-- IR: double (nullable = true)
 |-- TRANSACTION_AMOUNT: double (nullable = true)
 |-- TERM: integer (nullable = true)
 |-- ORIGINATION_DATE: date (nullable = true)
 |-- ORIGINAL_MATURITY_DATE: date (nullable = true)
 |-- LOAN_AMOUNT: double (nullable = true)
 |-- PRINCIPAL_BALANCE: double (nullable = true)
 |-- TRANSACTION_DATE: date (nullable = true)
 |-- REVERSAL_DATE: date (nullable = true)
 |-- REVERSAL_AMOUNT: double (nullable = true)
 |-- EARLY_PAID_AT: date (nullable = true)
 |-- SOLD_DATE: date (nullable = true)
 |-- TRANSREFNO: string (nullable = true)
 |-- MAX_REPORT_DATE: date (nullable = true)
 |-- MAX_DWH_TIMESTAMP: timestamp (nullable = true)
 |-- AMORT_TYPE: string (nullable = true)
 |-- MONTH_NUM: integer (nullable = true)
 |-- IPMT: float (nullable = true)
 |-- PERIOD_START_DATE: date (nullable = true)
 |-- DAYS_OF_PERIOD: integer (nullable = true)
 |-- DAY_NUM: integer (null

In [0]:
orig_fee_amort = sold_amort.unionAll(base_amort).unionAll(accel_amort).unionAll(reverse_amort).unionAll(df_old_keep)

In [0]:
orig_fee_report = orig_fee_amort.select(col('LOAN_ID'),
                                col('ORIGINATING_BANK'),
                                col('REPORT_DATE'),
                                col('TRANSACTION_AMOUNT'),
                                col('ORIG_FEE_AMORT'),
                                col('CUM_ORIG_FEE_AMORT'),
                                col('DEFERRED_ORIG_FEE'),
                                col('LOAN_SALE_ENDING_BAL'),
                                col('REVERSAL_AFTER_SOLD_LOAN')
                               )

orig_fee_report = orig_fee_report.groupBy('LOAN_ID','ORIGINATING_BANK','REPORT_DATE').agg(max('TRANSACTION_AMOUNT').alias('TRANSACTION_AMOUNT'),sum('ORIG_FEE_AMORT').alias('ORIG_FEE_AMORT'),sum('CUM_ORIG_FEE_AMORT').alias('CUM_ORIG_FEE_AMORT'),sum('DEFERRED_ORIG_FEE').alias('DEFERRED_ORIG_FEE'),sum('LOAN_SALE_ENDING_BAL').alias('LOAN_SALE_ENDING_BAL'),sum('REVERSAL_AFTER_SOLD_LOAN').alias('REVERSAL_AFTER_SOLD_LOAN'))

In [0]:
print('Old Loans:',df_base.select(col('LOAN_ID')).distinct().count()
    ,'\nUpdate Sold Loans:',sold_amort.select(col('LOAN_ID')).distinct().count()
    ,'\nUpdate Paid-Off Loans:',accel_amort.select(col('LOAN_ID')).distinct().count()
    ,'\nUpdate Reversed Loans:',reverse_amort.select(col('LOAN_ID')).distinct().count()
    ,'\nUpdate Baseline Loans:',base_amort.select(col('LOAN_ID')).distinct().count()
    ,'\nTotal New Record:',orig_fee_amort.select(col('LOAN_ID')).distinct().count())

Old Loans: 303535 
Update Sold Loans: 3 
Update Paid-Off Loans: 5 
Update Reversed Loans: 0 
Update Baseline Loans: 0 
Total New Record: 303535


In [0]:
print('Old Record:',df_base.count()
    ,'\nUpdate Record:',df_amort.count()
    ,'\nTotal New Record:',orig_fee_amort.count())

Old Record: 62802907 
Update Record: 5656 
Total New Record: 62802422


In [0]:
orig_fee_amort.write.option("mergeSchema", "true").mode("overwrite").saveAsTable('hive_metastore.analytics.orig_fee_amort_raw_check')

In [0]:
orig_fee_report.write.mode("overwrite").saveAsTable('hive_metastore.analytics.orig_fee_amort')

In [0]:
#baseline
#display(df1.filter(col('loan_id')=='64847700'))
#display(base_report.filter(col('loan_id')=='64847700'))

In [0]:
# reversal 
# accelerated + new transaction date
#display(df1.filter(col('loan_id')=='62721387'))
#display(reverse_report.filter(col('loan_id')=='62721387'))
##display(accel_report.filter(col('loan_id')=='62721387'))

In [0]:
#display(df1.filter(col('loan_id')=='61440049'))
#display(reverse_report.filter(col('loan_id')=='61440049'))
#display(accel_report.filter(col('loan_id')=='61440049'))

In [0]:
# sold case
#display(df1.filter(col('loan_id')=='62639335'))
#display(sold_report.filter(col('loan_id')=='62639335'))

In [0]:
#reversal
# baseline + new transaction date
#display(df1.filter(col('loan_id')=='65030935'))
#display(reverse_report.filter(col('loan_id')=='65030935'))
#display(base_report.filter(col('loan_id')=='65030935'))


In [0]:
# reverse > early paid at
#display(df1.filter(col('loan_id')=='54075652'))
#display(reverse_report.filter(col('loan_id')=='54075652'))
#display(accel_report.filter(col('loan_id')=='54075652'))


In [0]:
# sold loan with late reversal
#display(df1.filter(col('loan_id')=='65240701'))
#display(sold_report.filter(col('loan_id')=='65240701'))